In [1]:
import warnings
import polars as pl
import altair as alt

In [2]:
from src.kristi_promin import kristi_promin
from src.me_to_neurazi import me_to_neurazi
from src.alt_friendly import alt_friendly

In [3]:
alt.themes.register('irozhlas', kristi_promin)
alt.themes.enable('irozhlas')
warnings.filterwarnings('ignore')

In [4]:
pl.Config(tbl_rows=30)

In [5]:
df = pl.read_parquet(
    'data/papezstvo.parquet', use_pyarrow=True
).join(
    pl.read_json('data/papezstvo_rozsah_wikistranek.json'), on='id', how='left'
)

In [10]:
def presnost(x):
    if x == 11:
        return "na den"
    elif x < 11:
        return "na měsíc až rok"
#    elif x == "-":
#        return "neznámé"

In [11]:
def presnost_vatikan(x):
    if x == 2:
        return "na den"
    elif x == 1:
        return "na měsíc až rok"
    elif x == 0:
        "na několik let"
#    elif x == "-":
#        return "neznámé"

In [12]:
sirka = 350
vyska = 50
barva = '#B72D0D'

In [63]:
preciznost = alt.Chart(
    df.with_columns(
        pl.col("narozeni_presnost").map_elements(presnost, return_dtype=str).fill_null('méně nebo vůbec').alias("presnost")
    ).to_pandas(), 
    title=alt.Title(
        "S jakou přesností známe datum narození",
        subtitle=["Červená: datum známé na den, oranžová: na rok, šedá: méně či vůbec.",
                 'Zdrojem je databáze Wikidata.']
    ),
    width=sirka
).mark_bar(
).encode(
    alt.X("pontifikat_zacatek:T", title=None),
    alt.X2("pontifikat_konec:T", title=None),
    alt.Color(
        "presnost:N", 
        sort=["na den","na měsíc až rok","méně nebo vůbec"], 
        scale=alt.Scale(range=['#D6534B','#E99A2B','#F1D1BB']), 
        legend=None
    ),
)

preciznost

alt.Chart(...)

In [55]:
preciznost_vat = alt.Chart(
    df.with_columns(
        pl.col("vatikan_pontifikat_zacatek_presnost").map_elements(presnost_vatikan, return_dtype=str).fill_null('méně nebo vůbec').alias("presnost")
    ).to_pandas(),
    title=alt.Title(
        "S jakou přesností známe datum uvedení do úřadu",
        subtitle=['Červená: datum známé na den, oranžová: na rok, šedá: na několik let.',
                 'Zdrojem jsou webové stránky papežova úřadu.']
    ),
    width=sirka
).mark_bar(
).encode(
    alt.X("pontifikat_zacatek:T", title=None),
    alt.X2("pontifikat_konec:T", title=None),
    alt.Color(
        "presnost:N", 
        sort=["na den","na měsíc až rok","na několik let"], 
        scale=alt.Scale(range=['#D6534B','#E99A2B','#F1D1BB']), 
        legend=None
    ),
)

preciznost_vat

alt.Chart(...)

In [15]:
df.filter(pl.col("vatikan_pontifikat_zacatek_presnost") == 0).tail()

shape: (5, 34)
┌──────────────┬──────────────┬──────────────┬──────────────┬───┬──────────────┬──────────────┬─────────────┬──────────┐
│ vatikan_pora ┆ vatikan_jmen ┆ vatikan_pont ┆ vatikan_pont ┆ … ┆ narozeni_sou ┆ narozeni_zem ┆ delka_stran ┆ podhesla │
│ di           ┆ o            ┆ ifikat_zacat ┆ ifikat_konec ┆   ┆ radnice      ┆ e            ┆ ky          ┆ ---      │
│ ---          ┆ ---          ┆ ek           ┆ ---          ┆   ┆ ---          ┆ ---          ┆ ---         ┆ i64      │
│ i64          ┆ str          ┆ ---          ┆ str          ┆   ┆ struct[2]    ┆ str          ┆ i64         ┆          │
│              ┆              ┆ str          ┆              ┆   ┆              ┆              ┆             ┆          │
╞══════════════╪══════════════╪══════════════╪══════════════╪═══╪══════════════╪══════════════╪═════════════╪══════════╡
│ 10           ┆ Pius I       ┆ 0146-01-01   ┆ 0161-01-01   ┆ … ┆ {45.766667,1 ┆ Italy        ┆ 14506       ┆ 0        │
│              ┆              ┆              ┆              ┆   ┆ 3.366667}    ┆              ┆             ┆          │
│ 11           ┆ Anicetus     ┆ 0157-01-01   ┆ 0168-01-01   ┆ … ┆ {34.733333,3 ┆ Syria        ┆ 13875       ┆ 0        │
│              ┆              ┆              ┆              ┆   ┆ 6.716667}    ┆              ┆             ┆          │
│ 12           ┆ Soterus      ┆ 0168-01-01   ┆ 0177-01-01   ┆ … ┆ {41.35,13.41 ┆ Italy        ┆ 14000       ┆ 0        │
│              ┆              ┆              ┆              ┆   ┆ 6667}        ┆              ┆             ┆          │
│ 13           ┆ Eleutherius  ┆ 0177-01-01   ┆ 0193-01-01   ┆ … ┆ {39.00933,20 ┆ Greece       ┆ 21839       ┆ 1        │
│              ┆              ┆              ┆              ┆   ┆ .73353}      ┆              ┆             ┆          │
│ 14           ┆ Victor I     ┆ 0189-01-01   ┆ 0201-01-01   ┆ … ┆ {31.8,12.74} ┆ Ancient Rome ┆ 22718       ┆ 0        │
└──────────────┴──────────────┴──────────────┴──────────────┴───┴──────────────┴──────────────┴─────────────┴──────────┘

In [49]:
mnohost = alt.Chart(
    df.with_columns(pl.col("wikihesla").map_elements(len)).to_pandas(),
    title=alt.Title(
        "V kolika jazycích mají papežové heslo na Wikipedii",
        subtitle=['Prvního římského biskupa, Svatého Petra, překonávají globálním zásahem',
                  'pouze tři poslední papežové: Jan Pavel II., Benedikt XVI. a František I.']
    ),
    width=sirka, height=vyska
).mark_line(color=barva
).encode(
    alt.X("pontifikat_zacatek:T", title=None,),
    alt.X2("pontifikat_konec:T", title=None),
    alt.Y("wikihesla:Q", title=None, axis=alt.Axis(orient="right"))
)

mnohost

alt.Chart(...)

In [17]:
df.with_columns(pl.col("wikihesla").map_elements(len)).sort(by="wikihesla",descending=True).head(10).select(pl.col(['poradi','jmeno','wikihesla']))

shape: (10, 3)
┌────────┬───────────────┬───────────┐
│ poradi ┆ jmeno         ┆ wikihesla │
│ ---    ┆ ---           ┆ ---       │
│ u32    ┆ str           ┆ i64       │
╞════════╪═══════════════╪═══════════╡
│ 265    ┆ František     ┆ 171       │
│ 264    ┆ Benedikt XVI. ┆ 149       │
│ 263    ┆ Jan Pavel II. ┆ 146       │
│ 1      ┆ svatý Petr    ┆ 129       │
│ 260    ┆ Jan XXIII.    ┆ 110       │
│ 262    ┆ Jan Pavel I.  ┆ 109       │
│ 261    ┆ Pavel VI.     ┆ 107       │
│ 258    ┆ Pius XI.      ┆ 100       │
│ 259    ┆ Pius XII.     ┆ 98        │
│ 257    ┆ Benedikt XV.  ┆ 96        │
└────────┴───────────────┴───────────┘

In [361]:
barva_podbarveni = '#E99A2B'

do_grafu = df.with_columns(
    pl.when(
        pl.col('vatikan_poradi') == 214
    ).then(
        pl.lit("Alexandr VI.")
    ).when(
        pl.col('vatikan_poradi') == 169
    ).then(
        pl.lit("Hadrián IV.")
    ).when(
        pl.col('vatikan_poradi') == 64
    ).then(
        pl.lit("Řehoř I. Veliký")
    ).when(
        pl.col('vatikan_poradi') == 262
    ).then(
        pl.lit('Pavel VI.')
    ).when(
        pl.col('vatikan_poradi') == 264
    ).then(
        pl.lit('Jan Pavel II.')
    ).when(
        pl.col('vatikan_poradi') == 260
    ).then(
        pl.lit('Pius XII.')
    ).when(
        pl.col('vatikan_poradi') == 255
    ).then(
        pl.lit('Pius IX.')
    ).when(
        pl.col('vatikan_poradi') == 259
    ).then(
        pl.lit('Pius XI.')
    ).otherwise(None).alias("poznamka_pocet_stran")
).with_columns(
    pl.when(
        pl.col('vatikan_poradi') == 1
    ).then(
        pl.lit('sv. Petr')
    ).when(
        pl.col('vatikan_poradi') == 216
    ).then(
        pl.lit('Julius II.')
    ).when(
        pl.col('vatikan_poradi') == 265
    ).then(
        pl.lit('Benedikt XVI.')
    ).when(
        pl.col('vatikan_poradi') == 266
    ).then(
        pl.lit('František.')
    ).alias(
        'popisek_vpravo'
    )
).with_columns(
    pl.when(pl.col('jmeno').is_in(['Pius IX.'])).then(pl.lit("Piux IX.")).otherwise(None).alias("poznamka_pocet_odbocek")
).with_columns(
    pl.col("delka_stranky") / 1800
)

In [245]:
do_grafu.filter(~pl.col('poznamka_pocet_stran').is_null())

shape: (3, 36)
┌──────────────┬──────────────┬──────────────┬──────────────┬───┬──────────────┬──────────┬──────────────┬─────────────┐
│ vatikan_pora ┆ vatikan_jmen ┆ vatikan_pont ┆ vatikan_pont ┆ … ┆ delka_strank ┆ podhesla ┆ poznamka_poc ┆ poznamka_po │
│ di           ┆ o            ┆ ifikat_zacat ┆ ifikat_konec ┆   ┆ y            ┆ ---      ┆ et_stran     ┆ cet_odbocek │
│ ---          ┆ ---          ┆ ek           ┆ ---          ┆   ┆ ---          ┆ i64      ┆ ---          ┆ ---         │
│ i64          ┆ str          ┆ ---          ┆ str          ┆   ┆ f64          ┆          ┆ str          ┆ str         │
│              ┆              ┆ str          ┆              ┆   ┆              ┆          ┆              ┆             │
╞══════════════╪══════════════╪══════════════╪══════════════╪═══╪══════════════╪══════════╪══════════════╪═════════════╡
│ 169          ┆ Adrian IV    ┆ 1154-11-05   ┆ 1159-08-01   ┆ … ┆ 87.632222    ┆ 0        ┆ Adrian IV.   ┆ null        │
│ 214          ┆ Alexander VI ┆ 1492-07-26   ┆ 1503-07-18   ┆ … ┆ 46.502778    ┆ 2        ┆ Alexandr VI. ┆ null        │
│              ┆              ┆              ┆              ┆   ┆              ┆          ┆ a Julius II. ┆             │
│ 216          ┆ Julius II    ┆ 1503-10-26   ┆ 1513-01-21   ┆ … ┆ 47.911111    ┆ 5        ┆ Alexandr VI. ┆ null        │
│              ┆              ┆              ┆              ┆   ┆              ┆          ┆ a Julius II. ┆             │
└──────────────┴──────────────┴──────────────┴──────────────┴───┴──────────────┴──────────┴──────────────┴─────────────┘

In [149]:
df.filter(pl.col('jmeno').is_in(['Julius II.','Alexander VI.']))

shape: (1, 34)
┌──────────────┬──────────────┬──────────────┬──────────────┬───┬──────────────┬──────────────┬─────────────┬──────────┐
│ vatikan_pora ┆ vatikan_jmen ┆ vatikan_pont ┆ vatikan_pont ┆ … ┆ narozeni_sou ┆ narozeni_zem ┆ delka_stran ┆ podhesla │
│ di           ┆ o            ┆ ifikat_zacat ┆ ifikat_konec ┆   ┆ radnice      ┆ e            ┆ ky          ┆ ---      │
│ ---          ┆ ---          ┆ ek           ┆ ---          ┆   ┆ ---          ┆ ---          ┆ ---         ┆ i64      │
│ i64          ┆ str          ┆ ---          ┆ str          ┆   ┆ struct[2]    ┆ str          ┆ i64         ┆          │
│              ┆              ┆ str          ┆              ┆   ┆              ┆              ┆             ┆          │
╞══════════════╪══════════════╪══════════════╪══════════════╪═══╪══════════════╪══════════════╪═════════════╪══════════╡
│ 216          ┆ Julius II    ┆ 1503-10-26   ┆ 1513-01-21   ┆ … ┆ {44.339503,8 ┆ Italy        ┆ 86240       ┆ 5        │
│              ┆              ┆              ┆              ┆   ┆ .510133}     ┆              ┆             ┆          │
└──────────────┴──────────────┴──────────────┴──────────────┴───┴──────────────┴──────────────┴─────────────┴──────────┘

In [377]:
rozsah_podklad = alt.Chart(
    do_grafu.to_pandas(),
    title=alt.Title(
        "Co o papežích víme / jak nás dnes zajímají",
        subtitle=[
            ""
        ]),
    width=sirka, height=vyska * 3
).mark_line(color=barva
).encode(
    alt.X("pontifikat_zacatek:T", title=None,),
    alt.X2("pontifikat_konec:T", title=None),
    alt.Y("delka_stranky:Q", title=None, axis=alt.Axis(orient="left")),
    alt.Size("podhesla:Q", scale=alt.Scale(range=[1,3]), legend=None)
)

rozsah_anotace = alt.Chart(
    do_grafu.filter(~pl.col("poznamka_pocet_stran").is_null()).to_pandas()
).mark_rect(color='white', opacity=0.5).encode(
    alt.X('pontifikat_zacatek:T',title=None),
    alt.X2("pontifikat_konec:T", title=None),
    # alt.Y('delka_stranky',title=None),
)

rozsah_text_vlevo = alt.Chart(
    do_grafu.filter(~pl.col("poznamka_pocet_stran").is_null()).unique(subset=["poznamka_pocet_stran"]).to_pandas()
).mark_text(color=barva, size=7, align="right", dx=-2, font='Asap').encode(
    alt.X('pontifikat_zacatek:T',title=None),
    alt.Y("delka_stranky:Q"),
    alt.Text("poznamka_pocet_stran:N", title=None),
    # alt.Y('delka_stranky',title=None),
)

rozsah_text_vpravo = alt.Chart(
    do_grafu.filter(~pl.col("popisek_vpravo").is_null()).to_pandas()
).mark_text(color=barva, size=7, align="left", dx=2, font='Asap').encode(
    alt.X('pontifikat_konec:T',title=None),
    alt.Y("delka_stranky:Q"),
    alt.Text("popisek_vpravo:N", title=None),
    # alt.Y('delka_stranky',title=None),
)

rozsah = rozsah_anotace + rozsah_podklad + rozsah_text_vlevo + rozsah_text_vpravo

rozsah_samostatne = rozsah.configure_axis().configure_view(stroke='transparent')

rozsah_samostatne

alt.LayerChart(...)

In [331]:
do_grafu.sort(by='delka_stranky',descending=True).select(pl.col('vatikan_jmeno','vatikan_poradi','vatikan_pontifikat_zacatek','delka_stranky')).head(20)

shape: (20, 4)
┌───────────────┬────────────────┬────────────────────────────┬───────────────┐
│ vatikan_jmeno ┆ vatikan_poradi ┆ vatikan_pontifikat_zacatek ┆ delka_stranky │
│ ---           ┆ ---            ┆ ---                        ┆ ---           │
│ str           ┆ i64            ┆ str                        ┆ f64           │
╞═══════════════╪════════════════╪════════════════════════════╪═══════════════╡
│ Francis       ┆ 266            ┆ 2013-02-19                 ┆ 130.707222    │
│ John Paul II  ┆ 264            ┆ 1978-09-22                 ┆ 125.940556    │
│ Pius XII      ┆ 260            ┆ 1939-02-12                 ┆ 102.578889    │
│ Benedict XVI  ┆ 265            ┆ 2005-03-24                 ┆ 99.007222     │
│ Adrian IV     ┆ 169            ┆ 1154-11-05                 ┆ 87.632222     │
│ Peter         ┆ 1              ┆ null                       ┆ 80.193889     │
│ Paul VI       ┆ 262            ┆ 1963-05-30                 ┆ 70.415        │
│ Pius XI       ┆ 259            ┆ 1922-01-12                 ┆ 55.661667     │
│ Gregory I     ┆ 64             ┆ 0590-08-03                 ┆ 50.705        │
│ John XXIII    ┆ 261            ┆ 1958-10-04                 ┆ 50.691111     │
│ Pius X        ┆ 257            ┆ 1903-07-09                 ┆ 50.606667     │
│ Julius II     ┆ 216            ┆ 1503-10-26                 ┆ 47.911111     │
│ Alexander VI  ┆ 214            ┆ 1492-07-26                 ┆ 46.502778     │
│ Pius IX       ┆ 255            ┆ 1846-05-21                 ┆ 44.928889     │
│ Leo XIII      ┆ 256            ┆ 1878-02-03                 ┆ 44.391111     │
│ Clement VII   ┆ 219            ┆ 1523-10-26                 ┆ 40.463333     │
│ Boniface VIII ┆ 193            ┆ null                       ┆ 40.368333     │
│ John Paul I   ┆ 263            ┆ 1978-08-03                 ┆ 39.365556     │
│ Benedict XV   ┆ 258            ┆ 1914-08-06                 ┆ 36.346667     │
│ Pius II       ┆ 210            ┆ 1458-08-03                 ┆ 34.916111     │
└───────────────┴────────────────┴────────────────────────────┴───────────────┘

In [265]:
podhesla_podklad = alt.Chart(
    df.to_pandas(),
    title=alt.Title(
        "Kolik podhesel má anglické heslo na Wikipedii",
        subtitle=[
            'V 19. století je skokanem Pius IX. (1846-1878). Životopisné odbočky se věnují',
            'ztrátě Papežského státu a de facto uvěznění papeže ve Vatikánu, navozování',
            'diplomatikých vztahů nebo rekordním 39 encyklikám.'
        ]),
    width=sirka, height=vyska
).mark_line(color=barva
).encode(
    alt.X("pontifikat_zacatek:T", title=None,),
    alt.X2("pontifikat_konec:T", title=None),
    alt.Y("podhesla:Q", title=None, axis=alt.Axis(orient="right"))
)

podhesla_anotace = alt.Chart(
    do_grafu.filter(~pl.col("poznamka_pocet_odbocek").is_null()).to_pandas()
).mark_rect(color=barva_podbarveni, opacity=0.5).encode(
    alt.X('pontifikat_zacatek:T',title=None),
    alt.X2("pontifikat_konec:T", title=None),
    # alt.Y('delka_stranky',title=None),
)

podhesla_text = alt.Chart(
    do_grafu.filter(~pl.col("poznamka_pocet_odbocek").is_null()).to_pandas()
).mark_text(color=barva, size=8, align="right", dx=-2).encode(
    alt.X('pontifikat_zacatek:T',title=None),
    alt.Y("podhesla:Q"),
    alt.Text("poznamka_pocet_odbocek:N", title=None),
    # alt.Y('delka_stranky',title=None),
)

podhesla = podhesla_anotace + podhesla_podklad + podhesla_text

podhesla

alt.LayerChart(...)

In [259]:
alt.VConcatChart(
    vconcat=(mnohost, rozsah, podhesla, preciznost_vat, preciznost),
    title="Kolik toho o papežích víme"
).configure_view(
    stroke='transparent').configure_axis(grid=False).resolve_scale(x='shared', color="independent")

alt.VConcatChart(...)

In [217]:
df.sort(by='delka_stranky',descending=True)

shape: (266, 34)
┌──────────────┬──────────────┬──────────────┬──────────────┬───┬──────────────┬──────────────┬─────────────┬──────────┐
│ vatikan_pora ┆ vatikan_jmen ┆ vatikan_pont ┆ vatikan_pont ┆ … ┆ narozeni_sou ┆ narozeni_zem ┆ delka_stran ┆ podhesla │
│ di           ┆ o            ┆ ifikat_zacat ┆ ifikat_konec ┆   ┆ radnice      ┆ e            ┆ ky          ┆ ---      │
│ ---          ┆ ---          ┆ ek           ┆ ---          ┆   ┆ ---          ┆ ---          ┆ ---         ┆ i64      │
│ i64          ┆ str          ┆ ---          ┆ str          ┆   ┆ struct[2]    ┆ str          ┆ i64         ┆          │
│              ┆              ┆ str          ┆              ┆   ┆              ┆              ┆             ┆          │
╞══════════════╪══════════════╪══════════════╪══════════════╪═══╪══════════════╪══════════════╪═════════════╪══════════╡
│ 266          ┆ Francis      ┆ 2013-02-19   ┆ 2025-03-21   ┆ … ┆ {-34.633333, ┆ Argentina    ┆ 235273      ┆ 23       │
│              ┆              ┆              ┆              ┆   ┆ -58.466667}  ┆              ┆             ┆          │
│ 264          ┆ John Paul II ┆ 1978-09-22   ┆ 2005-03-02   ┆ … ┆ {49.883333,1 ┆ Poland       ┆ 226693      ┆ 27       │
│              ┆              ┆              ┆              ┆   ┆ 9.5}         ┆              ┆             ┆          │
│ 260          ┆ Pius XII     ┆ 1939-02-12   ┆ 1958-09-09   ┆ … ┆ {41.893056,1 ┆ Italy        ┆ 184642      ┆ 18       │
│              ┆              ┆              ┆              ┆   ┆ 2.482778}    ┆              ┆             ┆          │
│ 265          ┆ Benedict XVI ┆ 2005-03-24   ┆ 2013-01-28   ┆ … ┆ {48.254,12.8 ┆ Germany      ┆ 178213      ┆ 23       │
│              ┆              ┆              ┆              ┆   ┆ 419}         ┆              ┆             ┆          │
│ 169          ┆ Adrian IV    ┆ 1154-11-05   ┆ 1159-08-01   ┆ … ┆ {51.755,-0.3 ┆ United       ┆ 157738      ┆ 0        │
│              ┆              ┆              ┆              ┆   ┆ 36}          ┆ Kingdom      ┆             ┆          │
│ 1            ┆ Peter        ┆ null         ┆ 0067-01-01   ┆ … ┆ {32.90995,35 ┆ Israel       ┆ 144349      ┆ 10       │
│              ┆              ┆              ┆              ┆   ┆ .630536}     ┆              ┆             ┆          │
│ 262          ┆ Paul VI      ┆ 1963-05-30   ┆ 1978-07-06   ┆ … ┆ {45.6,10.216 ┆ Italy        ┆ 126747      ┆ 16       │
│              ┆              ┆              ┆              ┆   ┆ 667}         ┆              ┆             ┆          │
│ 259          ┆ Pius XI      ┆ 1922-01-12   ┆ 1939-01-10   ┆ … ┆ {45.616667,9 ┆ Italy        ┆ 100191      ┆ 7        │
│              ┆              ┆              ┆              ┆   ┆ .216667}     ┆              ┆             ┆          │
│ 64           ┆ Gregory I    ┆ 0590-08-03   ┆ 0604-02-12   ┆ … ┆ {41.893056,1 ┆ Italy        ┆ 91269       ┆ 1        │
│              ┆              ┆              ┆              ┆   ┆ 2.482778}    ┆              ┆             ┆          │
│ 261          ┆ John XXIII   ┆ 1958-10-04   ┆ 1963-05-03   ┆ … ┆ {45.707222,9 ┆ Italy        ┆ 91244       ┆ 7        │
│              ┆              ┆              ┆              ┆   ┆ .499167}     ┆              ┆             ┆          │
│ 257          ┆ Pius X       ┆ 1903-07-09   ┆ 1914-07-20   ┆ … ┆ {45.7299,11. ┆ Italy        ┆ 91092       ┆ 7        │
│              ┆              ┆              ┆              ┆   ┆ 92}          ┆              ┆             ┆          │
│ 216          ┆ Julius II    ┆ 1503-10-26   ┆ 1513-01-21   ┆ … ┆ {44.339503,8 ┆ Italy        ┆ 86240       ┆ 5        │
│              ┆              ┆              ┆              ┆   ┆ .510133}     ┆              ┆             ┆          │
│ 214          ┆ Alexander VI ┆ 1492-07-26   ┆ 1503-07-18   ┆ … ┆ {38.988729,- ┆ Spain        ┆ 83705       ┆ 2        │
│              ┆              ┆              ┆              ┆   ┆ 0.519154}    ┆              ┆             ┆  

In [21]:
alt.Chart(
    df.filter(
        pl.col('pontifikat_zacatek').dt.year().is_between(1010,1080)
    ).with_columns(
        pl.col("vatikan_pontifikat_zacatek_presnost").map_elements(presnost_vatikan, return_dtype=str).fill_null('méně nebo vůbec').alias("presnost")
    ).to_pandas(),
    width=sirka
).mark_bar(
).encode(
    alt.X("pontifikat_zacatek:T", title=None),
    alt.X2("pontifikat_konec:T", title=None),
    alt.Color(
        "presnost:N", 
        sort=["na den","na měsíc až rok","na několik let"], 
        scale=alt.Scale(range=['#D6534B','#E99A2B','#F1D1BB']), 
        legend=None
    ),
)


alt.Chart(...)